In [2]:
import pandas as pd 
import matplotlib.pyplot as plt
import seaborn as sns

In [3]:
wwbi_country = pd.read_csv('../data/wwbi_country.csv')
wwbi_data = pd.read_csv('../data/wwbi_data.csv')
wwbi_series = pd.read_csv('../data/wwbi_series.csv')

# Preprocessing

In [4]:
# Keep only neccessary columns & 
wwbi_country_wage = wwbi_country[['country_code', 'short_name', 'region', 'income_group']]
wwbi_data_wage = wwbi_data[wwbi_data['indicator_code'] == 'BI.WAG.TOTL.GD.ZS']

# Drop country with missing regions and income groups in wwbi_country_wage
wwbi_country_wage = wwbi_country_wage.dropna(subset=['region', 'income_group'])

# Merge the dataframes on 'country_code'
wwbi_merged = pd.merge(wwbi_country_wage, wwbi_data_wage, on='country_code', how='inner')
wwbi_merged

country_code short_name                     region         income_group  \
0             ABW      Aruba  Latin America & Caribbean          High income   
1             ABW      Aruba  Latin America & Caribbean          High income   
2             ABW      Aruba  Latin America & Caribbean          High income   
3             ABW      Aruba  Latin America & Caribbean          High income   
4             ABW      Aruba  Latin America & Caribbean          High income   
...           ...        ...                        ...                  ...   
3630          ZWE   Zimbabwe         Sub-Saharan Africa  Lower middle income   
3631          ZWE   Zimbabwe         Sub-Saharan Africa  Lower middle income   
3632          ZWE   Zimbabwe         Sub-Saharan Africa  Lower middle income   
3633          ZWE   Zimbabwe         Sub-Saharan Africa  Lower middle income   
3634          ZWE   Zimbabwe         Sub-Saharan Africa  Lower middle income   

         indicator_code  year      value  
0     BI.WAG.TOTL.GD.ZS  2000   8.503107  
1     BI.WAG.TOTL.GD.ZS  2001   8.230285  
2     BI.WAG.TOTL.GD.ZS  2002   9.330809  
3     BI.WAG.TOTL.GD.ZS  2003   9.070884  
4     BI.WAG.TOTL.GD.ZS  2004  10.991002  
...                 ...   ...        ...  
3630  BI.WAG.TOTL.GD.ZS  2016  13.232838  
3631  BI.WAG.TOTL.GD.ZS  2017  10.853515  
3632  BI.WAG.TOTL.GD.ZS  2018   7.866549  
3633  BI.WAG.TOTL.GD.ZS  2019   3.749973  
3634  BI.WAG.TOTL.GD.ZS  2020   6.440993  

[3635 rows x 7 columns]

In [5]:
# Define order for the income_group 
income_order = ['High income', 'Upper middle income', 'Lower middle income', 'Low income']
wwbi_merged['income_group'] = pd.Categorical(wwbi_merged['income_group'], categories=income_order, ordered=True)

In [6]:
# Define order for regions
region_order = [
    'Europe & Central Asia',
    'Middle East & North Africa',
    'East Asia & Pacific',
    'South Asia',
    'Sub-Saharan Africa',
    'Latin America & Caribbean',
    'North America'
]
wwbi_merged['region'] = pd.Categorical(wwbi_merged['region'], categories=region_order, ordered=True)

# Visualization

In [ ]:
import numpy as np
import matplotlib.ticker
from matplotlib.lines import Line2D
from matplotlib.patches import Rectangle
from matplotlib.ticker import ScalarFormatter
import matplotlib.patheffects as path_effects

In [4]:
# My settings
plt.rcParams['figure.dpi'] = 900  
plt.rcParams['savefig.dpi'] = 900  
plt.rcParams['font.size'] = 12  
plt.rcParams['axes.titlesize'] = 14 
plt.rcParams['axes.labelsize'] = 14  
plt.rcParams['xtick.labelsize'] = 12  
plt.rcParams['ytick.labelsize'] = 12  
plt.rcParams['legend.fontsize'] = 12  


In [ ]:
colors = ['#FF6F00FF', '#C71000FF', '#008EA0FF', '#8A4198FF']
palette = {income: colors[i] for i, income in enumerate(income_order)}


# Create the figure
regions = region_order
num_regions = len(regions)
rows = 2
cols = (num_regions + 1) // rows  
fig, axes = plt.subplots(rows, cols, figsize=(15, 10), sharex=True)
axes = axes.flatten()

# Create subplot for each region
for i, region in enumerate(regions):
    if i < len(axes):  
        ax = axes[i]
        region_data = wwbi_merged[wwbi_merged['region'] == region]
        
        # Plot individual country lines 
        for country, country_data in region_data.groupby('country_code'):
            income_group = country_data['income_group'].iloc[0]
            country_data = country_data.sort_values('year')
            ax.plot(
                country_data['year'], 
                country_data['value'],
                color=palette[income_group],
                linewidth=0.25, 
                alpha=0.7
            )
        
        # Plot smooth trend lines 
        sns.lineplot(
            data=region_data,
            x='year',
            y='value',
            hue='income_group',
            palette=palette,
            linewidth=2.0,
            alpha=0.6,
            ax=ax,
            errorbar=('ci', 80), 
            err_style='band',
            err_kws={
                'alpha': 0.15,  
                'linewidth': 0, 
            },
            estimator=lambda x: np.mean(x),  
            n_boot=1000, 
            legend=False if i > 0 else True
        )
        
        # Y-tick and Y labels -----------------------------------------------------------------------
        # Set logarithmic scale for y-axis with improved tick formatting
        ax.set_yscale('log', base=2)
        ax.set_ylim(0.5, 46)
        ax.set_yticks([4, 6, 8, 12, 16, 32])
        
        # Format y-axis labels to remove scientific notation
        formatter = ScalarFormatter()
        formatter.set_scientific(False)
        ax.yaxis.set_major_formatter(formatter)
        
        # y-axis labels
        ax.set_ylabel('')
        
        # X-tick and X axis labels -----------------------------------------------------------------------
        ax.set_xticks([2000, 2005, 2010, 2015, 2020])
        ax.tick_params(axis='x', labelsize=9, labelbottom=True)
        ax.set_xlabel('')

        
        # Grid ---------------------------------------------------------------------
        # Enhanced grid styling
        ax.grid(True, which='major', linewidth=1., color='#E0E0E0', alpha=1)
        ax.grid(True, which='minor', linewidth=0.5, color='#EEEEEE', alpha=0.8, linestyle='--')
        
        # Ensure grid lines are behind the data
        ax.set_axisbelow(True)
        
        # Set specific x and y gridlines 
        ax.xaxis.set_major_locator(matplotlib.ticker.MultipleLocator(5))  
        ax.xaxis.set_minor_locator(matplotlib.ticker.MultipleLocator(2.5))  
        
        for spine in ax.spines.values():
            spine.set_visible(False)
            
        # Subplot Title ---------------------------------------------------------------------
        ax.set_title(
            region, 
            fontweight='bold', 
            fontsize=12,
            pad=10,
            color='#333333'
        )

        # Legend ---------------------------------------------------------------------
        # Move the legend from the first plot to the figure
        if i == 0:
            handles, labels = ax.get_legend_handles_labels()
            ax.get_legend().remove()


# Hide empty subplots 
for i in range(len(regions), len(axes)):
    axes[i].set_visible(False)
    
# Set the x-axis label for the entire figure
fig.text(
    -0.01, 
    0.5,   
    'Wage Bill as Percentage of GDP (%)',
    fontsize=12,
    color='#333333',
    fontweight='bold',
    rotation=90,
    ha='center',
    va='center'
)


# Figure title ---------------------------------------------------------------------
plt.suptitle(
    'Wage Bill as Percentage of GDP by Region and Income Group', 
    fontsize=20, 
    fontweight='bold',
    color='#333333',
    y=1.0
)

# Legend ---------------------------------------------------------------------
income_labels = ['High income', 'Upper middle income', 'Lower middle income', 'Low income']
custom_handles = []
custom_labels = []

for i, label in enumerate(income_labels):
    # Create a background rectangle patch with light color
    rect = Rectangle((0, 0), 20, 8, facecolor=colors[i], alpha=0.2)
    # Create a line with the solid color
    line = Line2D([0, 20], [4, 4], color=colors[i], linewidth=1.8)
    
    # Add to our handles and labels lists
    custom_handles.append((rect, line))
    custom_labels.append(label)

# Create a custom handler map for the rectangle+line combination
class HandlerRectLine(matplotlib.legend_handler.HandlerBase):
    def create_artists(self, legend, orig_handle, xdescent, ydescent, width, height, fontsize, trans):
        rect, line = orig_handle
        height_multiplier = 2 
        
        # Calculate vertical positioning to keep rectangle centered
        rect_height = height * height_multiplier
        y_offset = (height - rect_height) / 2  
        
        # Create rectangle with increased height
        rect = Rectangle(
            xy=(xdescent, ydescent + y_offset), 
            width=width, 
            height=rect_height, 
            facecolor=rect.get_facecolor(), 
            alpha=rect.get_alpha(),
            transform=trans
        )
        
        # Keep the line centered in the legend item
        line = Line2D(
            [xdescent, xdescent + width], 
            [ydescent + height/2, ydescent + height/2],
            color=line.get_color(),
            linewidth=line.get_linewidth(),
            transform=trans
        )
        
        return [rect, line]

# Create the legend with custom handlers
legend = fig.legend(
    custom_handles,
    custom_labels,
    handler_map={tuple: HandlerRectLine()},
    loc='lower right',
    title='Income group',
    title_fontsize=12,
    bbox_to_anchor=(0.92, 0.2),
    frameon=True,
    fancybox=False,
    shadow=False,
    fontsize=10,
    labelspacing=1, 
)

# Make the legend title bold
legend.get_title().set_fontweight('bold')
legend.get_title().set_ha('left')
# --------------------------------------------------------------------


# Adjust layout 
plt.tight_layout(rect=[0, 0.05, 0.98, 0.95])
plt.subplots_adjust(top=0.92, hspace=0.4, wspace=0.25)

# Save the figure 
plt.savefig('../viz/wage_bill_as_gdp.png', format='png', dpi=900, bbox_inches='tight')
plt.show()